In [1]:
##!pip install pandas 
##!pip install numpy 
##!pip install ydata-profiling

In [2]:
import pandas as pd
import numpy as np
from ydata_profiling import ProfileReport
import re
from warnings import filterwarnings
filterwarnings('ignore')

In [3]:
df = pd.read_csv('../data/iherb_hair_care_raw_dataset.csv') 

df.shape

(630, 12)

In [4]:
df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 630 entries, 0 to 629
Data columns (total 12 columns):
 #   Column           Non-Null Count  Dtype  
---  ------           --------------  -----  
 0   product_id       630 non-null    int64  
 1   product_name     630 non-null    object 
 2   brand_name       630 non-null    object 
 3   category         630 non-null    object 
 4   list_price       630 non-null    float64
 5   discount_price   630 non-null    float64
 6   sale_in_30days   252 non-null    float64
 7   rating           630 non-null    float64
 8   no_of_reviews    630 non-null    int64  
 9   first_available  630 non-null    object 
 10  rankings         630 non-null    object 
 11  stock_alert      70 non-null     object 
dtypes: float64(4), int64(2), object(6)
memory usage: 59.2+ KB


In [5]:
# Determine the number of unique elements of the dataset
df.nunique()

product_id         608
product_name       608
brand_name          11
category             4
list_price         269
discount_price     300
sale_in_30days      14
rating              13
no_of_reviews      338
first_available     50
rankings           416
stock_alert          3
dtype: int64

Out of 630 records, we identified 608 unique products. The remaining 22 instances are duplicates, which exist because a product can fall into multiple categories. Given our interest in understanding product distribution across categories, we have chosen to retain these duplicates in our dataset.

In [6]:
# Determine whether there are missing values
df.isnull().sum()

product_id           0
product_name         0
brand_name           0
category             0
list_price           0
discount_price       0
sale_in_30days     378
rating               0
no_of_reviews        0
first_available      0
rankings             0
stock_alert        560
dtype: int64

In [7]:
# Handle sale_in_30_days

# Check the range of sales_in_30days
min_value = df['sale_in_30days'].min()
max_value = df['sale_in_30days'].max()

# Display results
print(f"Minimum sale_in_30days: {min_value}")
print(f"Maximum sale_in_30days: {max_value}")

Minimum sale_in_30days: 100.0
Maximum sale_in_30days: 40000.0


We can see that only 40% of the products have data for sale_in_30_days, with values ranging from 100 to 40,000. Therefore, we choose to interpret that 60% of the scraped products did not have any sales in 30 days and we filled those none records with 0.

In [8]:

# Fill null values in 'sale_in_30days' with 0
df['sale_in_30days'] = df['sale_in_30days'].fillna(0)

# Change the data type of 'sale_in_30days' to integer
df['sale_in_30days'] = df['sale_in_30days'].astype(int)

# Fill null values in 'stock_alert' with the string "in stock"
df['stock_alert'] = df['stock_alert'].fillna("in stock")

# Change the data type of 'product_id to string
df['product_id'] = df['product_id'].astype(str)

# Change the data type of 'first_available' to date
df['first_available'] = pd.to_datetime(df['first_available'], format='%m/%Y')

df.head()

product_id                                       product_name    brand_name  \
0     108764  Mielle, Strengthening Shampoo, Rosemary Mint, ...        Mielle   
1       6419  Giovanni, Smooth As Silk™, Deep Moisture Shamp...      Giovanni   
2       6412  Giovanni, Tea Tree Triple Treat, Invigorating ...      Giovanni   
3     100354  SheaMoisture, Jamaican Black Castor Oil, Stren...  SheaMoisture   
4       6398  Giovanni, 50:50 Balanced™, Hydrating-Clarifyin...      Giovanni   

  category  list_price  discount_price  sale_in_30days  rating  no_of_reviews  \
0  Shampoo       95.93           95.93           10000     4.6          17806   
1  Shampoo       71.80           71.80            5000     4.5          60121   
2  Shampoo       71.80           71.80            5000     4.6          30287   
3  Shampoo       93.03           93.03            5000     4.5          33247   
4  Shampoo       71.80           71.80            2000     4.5          17385   

  first_available                                           rankings  \
0      2021-08-01  {'ranking_shampoo': 2, 'ranking_hair_care': 5,...   
1      2007-05-01  {'ranking_shampoo': 4, 'ranking_hair_care': 12...   
2      2007-05-01  {'ranking_shampoo': 8, 'ranking_hair_care': 20...   
3      2020-06-01  {'ranking_shampoo': 9, 'ranking_hair_care': 21...   
4      2007-05-01  {'ranking_shampoo': 15, 'ranking_hair_care': 4...   

  stock_alert  
0    in stock  
1    in stock  
2    in stock  
3    in stock  
4    in stock

In [9]:
# Function to extract volume in fl oz
def extract_floz(product_name):
    match = re.search(r'(\d+\.?\d*)\s*fl oz', product_name, re.IGNORECASE)
    return float(match.group(1)) if match else None

# Function to extract volume in ml
def extract_ml(product_name):
    match = re.search(r'(\d+\.?\d*)\s*ml', product_name, re.IGNORECASE)
    return float(match.group(1)) if match else None

# Function to extract weight in oz
def extract_oz(product_name):
    match = re.search(r'(\d+\.?\d*)\s*oz', product_name, re.IGNORECASE)
    return float(match.group(1)) if match else None

# Function to extract weight in g
def extract_g(product_name):
    match = re.search(r'(\d+\.?\d*)\s*g\)', product_name, re.IGNORECASE)
    return float(match.group(1)) if match else None

# Apply the function to the product_name column
df['volume_in_floz'] = df['product_name'].apply(extract_floz)
df['volume_in_ml'] = df['product_name'].apply(extract_ml)
df['weight_in_oz'] = df['product_name'].apply(extract_oz)
df['weight_in_g'] = df['product_name'].apply(extract_g)

# Display the updated DataFrame
df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 630 entries, 0 to 629
Data columns (total 16 columns):
 #   Column           Non-Null Count  Dtype         
---  ------           --------------  -----         
 0   product_id       630 non-null    object        
 1   product_name     630 non-null    object        
 2   brand_name       630 non-null    object        
 3   category         630 non-null    object        
 4   list_price       630 non-null    float64       
 5   discount_price   630 non-null    float64       
 6   sale_in_30days   630 non-null    int32         
 7   rating           630 non-null    float64       
 8   no_of_reviews    630 non-null    int64         
 9   first_available  630 non-null    datetime64[ns]
 10  rankings         630 non-null    object        
 11  stock_alert      630 non-null    object        
 12  volume_in_floz   452 non-null    float64       
 13  volume_in_ml     502 non-null    float64       
 14  weight_in_oz     176 non-null    float64  

In [10]:
# Check records without volumne or weight
missing_all_columns = df[
    df['volume_in_floz'].isna() &
    df['volume_in_ml'].isna() &
    df['weight_in_oz'].isna() &
    df['weight_in_g'].isna()
]

# Output results
if missing_all_columns.empty:
    print("No products are missing records in all specified columns.")
else:
    print("The following products are missing records in all specified columns:")
    print(missing_all_columns[['product_name', 'volume_in_floz', 'volume_in_ml', 'weight_in_oz', 'weight_in_g']])

The following products are missing records in all specified columns:
                                          product_name  volume_in_floz  \
367  Kitsch, Scalp Exfoliator, Terracotta, 1 Exfoli...             NaN   
417       Kitsch, Scalp Exfoliator, Grey, 1 Exfoliator             NaN   

     volume_in_ml  weight_in_oz  weight_in_g  
367           NaN           NaN          NaN  
417           NaN           NaN          NaN  


In [11]:
# Drop rows where without volumne or weight
df = df.dropna(subset=['volume_in_floz', 'volume_in_ml', 'weight_in_oz', 'weight_in_g'], how='all')

# Display the updated DataFrame
df.info()

<class 'pandas.core.frame.DataFrame'>
Index: 628 entries, 0 to 629
Data columns (total 16 columns):
 #   Column           Non-Null Count  Dtype         
---  ------           --------------  -----         
 0   product_id       628 non-null    object        
 1   product_name     628 non-null    object        
 2   brand_name       628 non-null    object        
 3   category         628 non-null    object        
 4   list_price       628 non-null    float64       
 5   discount_price   628 non-null    float64       
 6   sale_in_30days   628 non-null    int32         
 7   rating           628 non-null    float64       
 8   no_of_reviews    628 non-null    int64         
 9   first_available  628 non-null    datetime64[ns]
 10  rankings         628 non-null    object        
 11  stock_alert      628 non-null    object        
 12  volume_in_floz   452 non-null    float64       
 13  volume_in_ml     502 non-null    float64       
 14  weight_in_oz     176 non-null    float64       

In [12]:
# Identify products with volume in fl oz
products_with_floz = df[df['volume_in_floz'].notna()]['product_name']

# Check for corresponding records in volume in ml
missing_in_ml = df[df['product_name'].isin(products_with_floz) & df['volume_in_ml'].isna()]

# Output results
if missing_in_ml.empty:
    print("All products with volume in floz have corresponding records in volume in ml.")
else:
    print("The following products with volume in floz do not have corresponding records in volume in ml:")
    print(missing_in_ml[['product_name', 'volume_in_floz']])

All products with volume in floz have corresponding records in volume in ml.


In [13]:
# Identify products with weight in g
products_with_g = df[df['weight_in_g'].notna()]['product_name']

# Check for corresponding records in weight in oz
missing_in_oz = df[df['product_name'].isin(products_with_g) & df['weight_in_oz'].isna()]

# Output results
if missing_in_oz.empty:
    print("All products with weight in g have corresponding records in weight in oz.")
else:
    print("The following products with weight in g do not have corresponding records in weight_in_oz:")
    print(missing_in_oz[['product_name']])

All products with weight in g have corresponding records in weight in oz.


In [14]:
# Drop the specified columns
df = df.drop(columns=['weight_in_g', 'volume_in_floz'])
# Display the updated DataFrame
df.info()

<class 'pandas.core.frame.DataFrame'>
Index: 628 entries, 0 to 629
Data columns (total 14 columns):
 #   Column           Non-Null Count  Dtype         
---  ------           --------------  -----         
 0   product_id       628 non-null    object        
 1   product_name     628 non-null    object        
 2   brand_name       628 non-null    object        
 3   category         628 non-null    object        
 4   list_price       628 non-null    float64       
 5   discount_price   628 non-null    float64       
 6   sale_in_30days   628 non-null    int32         
 7   rating           628 non-null    float64       
 8   no_of_reviews    628 non-null    int64         
 9   first_available  628 non-null    datetime64[ns]
 10  rankings         628 non-null    object        
 11  stock_alert      628 non-null    object        
 12  volume_in_ml     502 non-null    float64       
 13  weight_in_oz     176 non-null    float64       
dtypes: datetime64[ns](1), float64(5), int32(1), int

In [15]:
# Filter for products with non-null values in both volume_in_ml and weight_in_oz
products_with_both = df[df['volume_in_ml'].notna() & df['weight_in_oz'].notna()]

# Return the resulting DataFrame
products_with_both.reset_index(drop=True, inplace=True) # Optional: reset index for cleaner output
products_with_both['ml_divide_oz'] = products_with_both['volume_in_ml'] / products_with_both['weight_in_oz']
products_with_both

product_id                                       product_name  \
0      125898  SheaMoisture, Men, Moisturizing Shampoo, Raw S...   
1      129805  Okay Pure Naturals, For Men, Shampoo, Hair & B...   
2      129804  Okay Pure Naturals, Shampoo, Conditioner & Tre...   
3      130199  Okay Pure Naturals, Men Professional 2-in-1 Sh...   
4      122802  Dove, Men+Care 3 n 1, Body + Face + Hair Wash ...   
5      134513  Camille Rose, Coconut Water Curl Cleanse, Hydr...   
6      130200  Okay Pure Naturals, Men Professional, 3-in-1 M...   
7      109677  Camille Rose, Clean Rinse, Moisturizing & Clar...   
8      130198  Okay Pure Naturals, Body Wash & Shampoo for Me...   
9      134528  Camille Rose, Coconut Water, Curl Coating Cowa...   
10     109667  Camille Rose, Curl Love Moisture Milk, Leave-I...   
11     134509  Camille Rose, Curl Love, Moisture Milk, 2 oz (...   
12     129804  Okay Pure Naturals, Shampoo, Conditioner & Tre...   
13     130199  Okay Pure Naturals, Men Professional 2-in-1 Sh...   
14     134500  Camille Rose, Black Castor Oil + Chebe, Deep C...   
15     134512  Camille Rose, Coconut Water, Curl Conditioner,...   
16     134529  Camille Rose, Strength, Restorative Deep Condi...   
17     135787  Camille Rose, Coconut Water, Hydrating Elixir,...   
18     134530  Camille Rose, Grace, Refreshing Moisture Mist,...   
19     130200  Okay Pure Naturals, Men Professional, 3-in-1 M...   
20     134519  Camille Rose, Caramel Cowash Cleansing Conditi...   
21     130202  Okay Pure Naturals, Miami South Beach Curls, C...   
22     130201  Okay Pure Naturals, Miami South Beach Curls, C...   
23     134505  Camille Rose, Leave-In Detangling Hair Treatme...   
24     119711  Kitsch, Pre-Wash Scalp Oil, Rosemary & Biotin,...   
25     109670  Camille Rose, Ultimate Strength Serum, Cocoa N...   
26     109684  Camille Rose, Mint Condition Braid & Scalp Spr...   
27     124726  Mielle, Anti-Shedding Gel Hair Masque, Sea Mos...   
28     129801  Okay Pure Naturals, Black Jamaican Castor Oil,...   
29     130195  Okay Pure Naturals, Coconut Hot Oil Treatment,...   
30     100208  Okay Pure Naturals, All Natural Coconut Oil, D...   
31     137611  Okay Pure Naturals, Argan Hot Oil Treatment, 6...   
32     129802  Okay Pure Naturals, Almond Hot Oil Treatment, ...   
33     134516  Camille Rose, Coconut Water, Penetrating Hair ...   
34     109671  Camille Rose, Algae Renew®, Deep Conditioning ...   
35     109667  Camille Rose, Curl Love Moisture Milk, Leave-I...   
36     109666          Camille Rose, Curl Maker®, 12 oz (355 ml)   
37     135786  Camille Rose, Curl Maker, Marshmallow & Agave ...   
38     134499  Camille Rose, Curlaide Moisture Butter, Green ...   
39     134501  Camille Rose, Fresh Curl Revitalizing Hair Smo...   
40     134506  Camille Rose, Black Castor Oil + Chebe, Butter...   
41     135787  Camille Rose, Coconut Water, Hydrating Elixir,...   
42     130203  Okay Pure Naturals, Miami South Beach Curls,  ...   
43     134517  Camille Rose, Coconut Water Style Setter, Maxi...   
44     130183  Okay Pure Naturals, Polished Edges With Black ...   
45     137599  Okay Pure Naturals, Miami South Beach Curls, S...   
46     130184  Okay Pure Naturals, On The Go Polished Edges W...   
47     130185  Okay Pure Naturals, On The Go Polished Edges W...   
48     134518  Camille Rose, Kids, Sweet Puddin' Mandarin Hai...   
49     109669  Camille Rose, Almond Jai Twisting Butter, Swee...   

            brand_name     category  list_price  discount_price  \
0         SheaMoisture      Shampoo       68.21           68.21   
1   Okay Pure Naturals      Shampoo       87.23           87.23   
2   Okay Pure Naturals      Shampoo      101.76          101.76   
3   Okay Pure Naturals      Shampoo       72.67           72.67   
4                 Dove      Shampoo       63.26           63.26   
5         Camille Rose      Shampoo      154.76          154.76   
6   Okay Pure Naturals      Shampoo       87.20           87.20  

In [16]:
# Calculate average ml_divide_oz by category
average_ml_divide_oz = products_with_both.groupby('category')['ml_divide_oz'].mean().reset_index()

# Rename the average column for clarity
average_ml_divide_oz.rename(columns={'ml_divide_oz': 'average_ml_divide_oz'}, inplace=True)

# Display the result including the category column
print(average_ml_divide_oz)

      category  average_ml_divide_oz
0  Conditioner             29.781845
1      Shampoo             29.466840
2      Styling             29.770000
3   Treatments             29.715909


In [17]:
print(df.columns)

Index(['product_id', 'product_name', 'brand_name', 'category', 'list_price',
       'discount_price', 'sale_in_30days', 'rating', 'no_of_reviews',
       'first_available', 'rankings', 'stock_alert', 'volume_in_ml',
       'weight_in_oz'],
      dtype='object')


In [18]:
print(average_ml_divide_oz.columns)

Index(['category', 'average_ml_divide_oz'], dtype='object')


In [19]:
# Merge the average back into the original DataFrame
df = df.merge(average_ml_divide_oz, on='category', how='left')
print(df.columns)

Index(['product_id', 'product_name', 'brand_name', 'category', 'list_price',
       'discount_price', 'sale_in_30days', 'rating', 'no_of_reviews',
       'first_available', 'rankings', 'stock_alert', 'volume_in_ml',
       'weight_in_oz', 'average_ml_divide_oz'],
      dtype='object')


In [20]:
# Fill null values in volume_in_ml
df['volume_in_ml'].fillna(df['weight_in_oz'] * df['average_ml_divide_oz'], inplace=True)
df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 628 entries, 0 to 627
Data columns (total 15 columns):
 #   Column                Non-Null Count  Dtype         
---  ------                --------------  -----         
 0   product_id            628 non-null    object        
 1   product_name          628 non-null    object        
 2   brand_name            628 non-null    object        
 3   category              628 non-null    object        
 4   list_price            628 non-null    float64       
 5   discount_price        628 non-null    float64       
 6   sale_in_30days        628 non-null    int32         
 7   rating                628 non-null    float64       
 8   no_of_reviews         628 non-null    int64         
 9   first_available       628 non-null    datetime64[ns]
 10  rankings              628 non-null    object        
 11  stock_alert           628 non-null    object        
 12  volume_in_ml          628 non-null    float64       
 13  weight_in_oz        

In [21]:
# Drop the specified columns
df = df.drop(columns=['weight_in_oz', 'average_ml_divide_oz'])
# Display the updated DataFrame
df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 628 entries, 0 to 627
Data columns (total 13 columns):
 #   Column           Non-Null Count  Dtype         
---  ------           --------------  -----         
 0   product_id       628 non-null    object        
 1   product_name     628 non-null    object        
 2   brand_name       628 non-null    object        
 3   category         628 non-null    object        
 4   list_price       628 non-null    float64       
 5   discount_price   628 non-null    float64       
 6   sale_in_30days   628 non-null    int32         
 7   rating           628 non-null    float64       
 8   no_of_reviews    628 non-null    int64         
 9   first_available  628 non-null    datetime64[ns]
 10  rankings         628 non-null    object        
 11  stock_alert      628 non-null    object        
 12  volume_in_ml     628 non-null    float64       
dtypes: datetime64[ns](1), float64(4), int32(1), int64(1), object(6)
memory usage: 61.5+ KB


In [22]:
# Add column price per ml
df['price_per_ml'] = (df['discount_price'] / df['volume_in_ml']).round(2)

# Add column disount %
df['discount%'] = ((df['list_price']-df['discount_price'])/df['list_price']*100).round(2)

# Add column sales revenue
df['sales_revenue'] = (df['discount_price']*df['sale_in_30days']).round(2)

# Display the updated DataFrame
df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 628 entries, 0 to 627
Data columns (total 16 columns):
 #   Column           Non-Null Count  Dtype         
---  ------           --------------  -----         
 0   product_id       628 non-null    object        
 1   product_name     628 non-null    object        
 2   brand_name       628 non-null    object        
 3   category         628 non-null    object        
 4   list_price       628 non-null    float64       
 5   discount_price   628 non-null    float64       
 6   sale_in_30days   628 non-null    int32         
 7   rating           628 non-null    float64       
 8   no_of_reviews    628 non-null    int64         
 9   first_available  628 non-null    datetime64[ns]
 10  rankings         628 non-null    object        
 11  stock_alert      628 non-null    object        
 12  volume_in_ml     628 non-null    float64       
 13  price_per_ml     628 non-null    float64       
 14  discount%        628 non-null    float64  

In [23]:
# Transform the 'rankings' column from stringified dictionaries into expanded columns
df['rankings'] = df['rankings'].apply(lambda x: eval(x))
rankings_columns = df['rankings'].apply(pd.Series)
df = pd.concat([df, rankings_columns], axis=1)

# Drop the original rankings column as it is no longer needed
df.drop(columns=['rankings'], inplace=True)

In [24]:
# Select and reorder the required columns
new_order = ['product_id','product_name','brand_name','category','volume_in_ml','list_price','discount_price', 'price_per_ml', 'discount%', 'sale_in_30days', 'sales_revenue','rating','no_of_reviews','first_available','stock_alert', 'ranking_shampoo', 'ranking_conditioner','ranking_hair_treatments','ranking_hair_styling']
df = df[new_order]

# Descriptive statistics
df.describe()

volume_in_ml  list_price  discount_price  price_per_ml   discount%  \
count    628.000000  628.000000      628.000000    628.000000  628.000000   
mean     293.899753   89.457006       86.454283      0.421178    2.915159   
min       30.000000   15.990000       15.690000      0.090000    0.000000   
25%      178.538864   66.847500       64.700000      0.200000    0.000000   
50%      273.000000   82.860000       79.950000      0.290000    0.000000   
75%      384.000000  105.757500      101.690000      0.480000    0.000000   
max      750.000000  305.110000      305.110000      3.140000   53.570000   
std      157.847749   38.663621       37.440069      0.380758    8.642664   

       sale_in_30days  sales_revenue      rating  no_of_reviews  \
count      628.000000   6.280000e+02  628.000000     628.000000   
mean       329.060510   2.779982e+04    4.561465    1993.966561   
min          0.000000   0.000000e+00    3.800000       1.000000   
25%          0.000000   0.000000e+00    4.500000      21.000000   
50%          0.000000   0.000000e+00    4.600000      87.500000   
75%        200.000000   1.436250e+04    4.700000     579.000000   
max      40000.000000   3.852400e+06    5.000000   60121.000000   
std       1819.911203   1.722146e+05    0.187859    6808.951769   

                     first_available  ranking_shampoo  ranking_conditioner  \
count                            628       153.000000           206.000000   
mean   2022-03-23 07:08:47.388535040       313.771242           284.131068   
min              2007-05-01 00:00:00         2.000000             2.000000   
25%              2021-09-01 00:00:00       176.000000           119.000000   
50%              2023-06-01 00:00:00       310.000000           282.000000   
75%              2023-09-01 00:00:00       447.000000           420.000000   
max              2024-08-01 00:00:00       660.000000           608.000000   
std                              NaN       185.993156           178.039889   

       ranking_hair_treatments  ranking_hair_styling  
count               142.000000            139.000000  
mean                302.014085            134.942446  
min                   1.000000              2.000000  
25%                 154.000000             52.000000  
50%                 314.000000            129.000000  
75%                 450.000000            209.000000  
max                 572.000000            292.000000  
std                 169.674740             88.878093

In [25]:
start_index = 16 if len(df.columns) >= 17 else 0

# Convert non-missing values to string, removing any trailing '.0'
for col in df.columns[start_index:]:
    df[col] = df[col].apply(lambda x: str(int(x)) if pd.notnull(x) and x == int(x) else str(x) if pd.notnull(x) else x)

df.head()

product_id                                       product_name    brand_name  \
0     108764  Mielle, Strengthening Shampoo, Rosemary Mint, ...        Mielle   
1       6419  Giovanni, Smooth As Silk™, Deep Moisture Shamp...      Giovanni   
2       6412  Giovanni, Tea Tree Triple Treat, Invigorating ...      Giovanni   
3     100354  SheaMoisture, Jamaican Black Castor Oil, Stren...  SheaMoisture   
4       6398  Giovanni, 50:50 Balanced™, Hydrating-Clarifyin...      Giovanni   

  category  volume_in_ml  list_price  discount_price  price_per_ml  discount%  \
0  Shampoo         355.0       95.93           95.93          0.27        0.0   
1  Shampoo         250.0       71.80           71.80          0.29        0.0   
2  Shampoo         250.0       71.80           71.80          0.29        0.0   
3  Shampoo         384.0       93.03           93.03          0.24        0.0   
4  Shampoo         250.0       71.80           71.80          0.29        0.0   

   sale_in_30days  sales_revenue  rating  no_of_reviews first_available  \
0           10000       959300.0     4.6          17806      2021-08-01   
1            5000       359000.0     4.5          60121      2007-05-01   
2            5000       359000.0     4.6          30287      2007-05-01   
3            5000       465150.0     4.5          33247      2020-06-01   
4            2000       143600.0     4.5          17385      2007-05-01   

  stock_alert  ranking_shampoo ranking_conditioner ranking_hair_treatments  \
0    in stock              2.0                 NaN                     NaN   
1    in stock              4.0                 NaN                     NaN   
2    in stock              8.0                 NaN                     NaN   
3    in stock              9.0                 NaN                     NaN   
4    in stock             15.0                 NaN                     NaN   

  ranking_hair_styling  
0                  NaN  
1                  NaN  
2                  NaN  
3                  NaN  
4                  NaN

In [26]:
product_column = ['product_id', 'product_name','brand_name','category']
df_2 = df[product_column]
df_2.head()

product_id                                       product_name    brand_name  \
0     108764  Mielle, Strengthening Shampoo, Rosemary Mint, ...        Mielle   
1       6419  Giovanni, Smooth As Silk™, Deep Moisture Shamp...      Giovanni   
2       6412  Giovanni, Tea Tree Triple Treat, Invigorating ...      Giovanni   
3     100354  SheaMoisture, Jamaican Black Castor Oil, Stren...  SheaMoisture   
4       6398  Giovanni, 50:50 Balanced™, Hydrating-Clarifyin...      Giovanni   

  category  
0  Shampoo  
1  Shampoo  
2  Shampoo  
3  Shampoo  
4  Shampoo

In [27]:
# Function to remove brand and category from product_name
def remove_words(row):
    product_name = row['product_name']
    brand = row['brand_name']
    category = row['category']
    # Remove brand and category from product_name
    for word in [brand, category]:
        product_name = product_name.replace(word, '')
    # Strip any extra whitespace
    return ' '.join(product_name.split())

# Apply the function to df_2
df_2['product_name'] = df_2.apply(remove_words, axis=1)

# Display the updated DataFrame
df_2.head()

product_id                                       product_name    brand_name  \
0     108764  , Strengthening , Rosemary Mint, 12 fl oz (355...        Mielle   
1       6419  , Smooth As Silk™, Deep Moisture , For Damaged...      Giovanni   
2       6412  , Tea Tree Triple Treat, Invigorating , For Al...      Giovanni   
3     100354  , Jamaican Black Castor Oil, Strengthen & Rest...  SheaMoisture   
4       6398  , 50:50 Balanced™, Hydrating-Clarifying , For ...      Giovanni   

  category  
0  Shampoo  
1  Shampoo  
2  Shampoo  
3  Shampoo  
4  Shampoo

In [28]:
# Function to clean up product_name
def clean_product_name(name):
    # Remove the first comma
    name = name.replace(',', '', 1)  # Remove the first occurrence of a comma
    
    # Remove the final comma and everything after it
    if ',' in name:
        name = name.rsplit(',', 1)[0]  # Keep everything before the last comma
    
    # Strip whitespace and return the cleaned name
    return name.strip()

# Apply the cleaning function to the product_name column
df_2['product_name'] = df_2['product_name'].apply(clean_product_name)

# Split product_name by comma into separate columns
# Since we cleaned product_name, we can now split it
df_split = df_2['product_name'].str.split(',', expand=True)

# Rename the new columns for clarity
df_split.columns = [f'product_name_part_{i+1}' for i in range(df_split.shape[1])]

# Concatenate the original DataFrame with the new split columns
df_2 = pd.concat([df_2, df_split], axis=1)

# Display the updated DataFrame
df_2.head()

product_id                                       product_name    brand_name  \
0     108764                      Strengthening , Rosemary Mint        Mielle   
1       6419  Smooth As Silk™, Deep Moisture , For Damaged Hair      Giovanni   
2       6412  Tea Tree Triple Treat, Invigorating , For All ...      Giovanni   
3     100354    Jamaican Black Castor Oil, Strengthen & Restore  SheaMoisture   
4       6398  50:50 Balanced™, Hydrating-Clarifying , For No...      Giovanni   

  category        product_name_part_1     product_name_part_2  \
0  Shampoo             Strengthening            Rosemary Mint   
1  Shampoo            Smooth As Silk™          Deep Moisture    
2  Shampoo      Tea Tree Triple Treat           Invigorating    
3  Shampoo  Jamaican Black Castor Oil    Strengthen & Restore   
4  Shampoo            50:50 Balanced™   Hydrating-Clarifying    

       product_name_part_3 product_name_part_4 product_name_part_5  \
0                     None                None                None   
1         For Damaged Hair                None                None   
2       For All Hair Types                None                None   
3                     None                None                None   
4   For Normal to Dry Hair                None                None   

  product_name_part_6  
0                None  
1                None  
2                None  
3                None  
4                None

In [29]:
# Export the processed data to a csv file
file_path_1 = '../data/iherb_hair_care_clean_dataset.csv'
file_path_2 = '../data/product_name_split.csv'
df.to_csv(file_path_1, index=False)
df_2.to_csv(file_path_2, index=False)

In [30]:
# Open a new dataframe for profiling report (without product_id and the ranking columns)
order = ['product_name','brand_name','category','volume_in_ml', 'discount_price', 'price_per_ml', 'discount%','sale_in_30days','rating','no_of_reviews','first_available', 'stock_alert']
df_3 = df[order]

# Generate the profile report
profile = ProfileReport(df_3, title="Profile Report for Hair Care Products")
profile.to_notebook_iframe()

Summarize dataset:   0%|          | 0/5 [00:00<?, ?it/s]

Generate report structure:   0%|          | 0/1 [00:00<?, ?it/s]

Render HTML:   0%|          | 0/1 [00:00<?, ?it/s]